# gpCAM Test Notebook
In this notebook we will go through many features of gpCAM. Work through it 
and you are ready for your own autonomous experiment. 

## This first cell has nothing to do with gpCAM, it's just a function to plot some results later

In [1]:
import plotly.graph_objects as go
import numpy as np
def plot(x,y,z,data = None):
    fig = go.Figure()
    fig.add_trace(go.Surface(x = x, y = y,z=z))
    if data is not None: 
        fig.add_trace(go.Scatter3d(x=data[:,0], y=data[:,1], z=data[:,2],
                                   mode='markers'))

    fig.update_layout(title='Posterior Mean', autosize=True,
                  width=800, height=800,
                  margin=dict(l=65, r=50, b=65, t=90))


    fig.show()

## Here we want to define some points at which we will predict, still has nothing to do with gpCAM 

In [2]:
x_pred = np.zeros((10000,2))
x = np.linspace(0,10,100)
y = np.linspace(0,10,100)
x,y = np.meshgrid(x,y)
counter = 0
for i in  range(100):
    for j in range(100):
        x_pred[counter] = np.array([x[i,j],y[i,j]])
        counter += 1

## Let's get after it by setting up a Single-Task GP Autonomous Data Acquisition Run

In [3]:
def optional_acq_func(x,obj):
    #this acquisition function makes the autonomous experiment a Bayesian optimization
    a = 3.0 #3.0 for 95 percent confidence interval
    mean = obj.posterior_mean(x)["f(x)"]
    cov = obj.posterior_covariance(x)["v(x)"]
    return mean + a * cov

def optional_cost_function(origin,x,arguments = None):
    #cost pf l1 motion in the input space
    offset = arguments["offset"]
    slope = arguments["slope"]
    d = np.abs(np.subtract(origin,x))
    c = (d * slope) + offset
    n = np.sum(c)
    return n
def optional_cost_update_function(costs, parameters):
    ###defining a cost update function might look tricky but just need a bit
    ###of tenacity. And remember, this is optional, if you have a great guess for your costs you
    ###don't need to update the costs. Also, if you don't account for costs, this funciton is not needed
    from scipy.optimize import differential_evolution as devo
    print("Cost adjustment in progress...")
    print("old cost parameters: ",parameters)
    bounds = np.array([[0.001,10],[0.0001,10]])
    ###remove outliers:
    origins = []
    points = []
    motions = []
    c   = []
    cost_per_motion = []
    for i in range(len(costs)):
        origins.append(costs[i][0])
        points.append(costs[i][1])
        motions.append(abs(costs[i][0] - costs[i][1]))
        c.append(costs[i][2])
        cost_per_motion.append(costs[i][2]/optional_cost_function(costs[i][0],costs[i][1], parameters))
    mean_costs_per_distance = np.mean(np.asarray(cost_per_motion))
    sd = np.std(np.asarray(cost_per_motion))
    for element in cost_per_motion:
        if (
            element >= mean_costs_per_distance - 2.0 * sd
            and element <= mean_costs_per_distance + 2.0 * sd
        ):
            continue
        else:
            motions.pop(cost_per_motion.index(element))
            c.pop(cost_per_motion.index(element))
            origins.pop(cost_per_motion.index(element))
            points.pop(cost_per_motion.index(element))
            cost_per_motion.pop(cost_per_motion.index(element))
    def compute_l1_cost_misfit(params, origins,points, costs):
        parameters = {"offset": params[0], "slope": params[1]}
        sum1 = 0.0
        for idx in range(len(points)):
            sum1 = sum1 + (
                (optional_cost_function(origins[idx],points[idx],parameters) - costs[idx]) ** 2)
        return sum1
    res = devo(compute_l1_cost_misfit, bounds, args = (origins, points,c), tol=1e-6, disp=True, maxiter=300, popsize=20,polish=False)
    arguments = {"offset": res["x"][0],"slope": res["x"][1:]}
    print("New cost parameters: ", arguments)
    return arguments

In [4]:
import time
from gpcam.autonomous_experimenter import AutonomousExperimenterGP

def instrument(data):
    for entry in data:
        entry["value"] = np.sin(np.linalg.norm(entry["position"]))
        entry["cost"]  = [np.array([0,0]),entry["position"],np.sum(entry["position"])]
    return data
#initialization
#feel free to try different acquisition functions, e.g. optional_acq_func, "covariance", "shannon_ig"
#note how costs are defined in for the autonomous experimenter
my_ae = AutonomousExperimenterGP(np.array([[0,10],[0,10]]),instrument,
                                 np.ones((3)),np.array([[0.001,100],[0.001,100],[0.001,100]]),
                                 init_dataset_size= 20, 
                                 acq_func = optional_acq_func, 
                                 #cost_func = optional_cost_function, 
                                 #cost_update_func = optional_cost_update_function,
                                 cost_func_params={"offset": 5.0,"slope":10.0})


print("length of the dataset: ",len(my_ae.x))

#training
#my_ae.train_async() #train asynchronously
my_ae.train()       #or not
#print("Initial training submitted")
#for i in range(2): #this loop shows how hyperparameters are changing if they are trained asynchronously
#    time.sleep(2)


New data communicated via tell()
CAUTION: you have not provided data variances in fvGP,
they will be set to 1 percent of the data values!
GP successfully initiated
Costs successfully initialized
##################################################################################
Initialization successfully concluded
now train(...) or train_async(...), and then go(...)
##################################################################################
length of the dataset:  20
fvGP training started with  20  data points
fvGP hyperparameter tuning in progress. Old hyperparameters:  [1. 1. 1.]  with old log likelihood:  22.219921110856703
method:  global
fvGP is performing a global differential evolution algorithm to find the optimal hyperparameters.
maximum number of iterations:  20
termination tolerance:  1e-06
bounds:  [[1.e-03 1.e+02]
 [1.e-03 1.e+02]
 [1.e-03 1.e+02]]
differential_evolution step 1: f(x)= 22.8817
differential_evolution step 2: f(x)= 22.8817
differential_evolution step 3

/home/marcus/VirtualEnvironments/gpCAM7/lib/python3.8/site-packages/numpy/core/_asarray.py:102: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  return array(a, dtype, copy=False, order=order)


## Let's see what our initial model looks like

In [5]:
f = my_ae.gp_optimizer.posterior_mean(x_pred)["f(x)"]
f_re = f.reshape(100,100)

plot(x,y,f_re, data = np.column_stack([my_ae.x,my_ae.y]))

## Let's run the autonomus loop to 100 points

In [6]:
#run the loop
my_ae.go(N = 100, acq_func_opt_setting = lambda number: "global" if number % 2 == 0 else "local",
            training_opt_callable = None,
            training_opt_max_iter = 20,
            training_opt_pop_size = 10,
            training_opt_tol      = 1e-6,
            acq_func_opt_max_iter = 20,
            acq_func_opt_pop_size = 20,
            acq_func_opt_tol      = 1e-6,
            acq_func_opt_tol_adjust = [True,0.1])#,update_cost_func_at = [30])
print("length of the dataset is now: ", len(my_ae.x))
#and that runs the autonomous loop

Date and time:        2021-07-20_16_35_06



iteration:  20
Run Time:  0.0003299713134765625      seconds
Number of measurements:  20
hps:  [0.45476156 1.04563354 2.87140214]
ask() initiated with hyperparameters: [0.45476156 1.04563354 2.87140214]
optimization method:  global
bounds:  None
finding acquisition function maxima...
optimization method  global
tolerance:  1e-06
population size:  20
maximum number of iterations:  20
bounds: 
[[ 0 10]
 [ 0 10]]
cost function parameters:  {'offset': 5.0, 'slope': 10.0}
differential_evolution step 1: f(x)= -1.50218
differential_evolution step 2: f(x)= -1.50218
differential_evolution step 3: f(x)= -1.50218
differential_evolution step 4: f(x)= -1.50218
differential_evolution step 5: f(x)= -1.50218
differential_evolution step 6: f(x)= -1.50218
differential_evolution step 7: f(x)= -1.50346
differential_evolution step 8: f(x)= -1.5045
differential_evolution step 9: f(x)= -1.50474
differential_evolution step 10: f(x)= -1.50474
differential_evolution 

/home/marcus/VirtualEnvironments/gpCAM7/lib/python3.8/site-packages/numpy/core/_asarray.py:102: VisibleDeprecationWarning:

Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.



differential_evolution step 1: f(x)= -1.46844
differential_evolution step 2: f(x)= -1.48017
differential_evolution step 3: f(x)= -1.48017
The acquisition function optimization resulted in: 
     x:  [[6.91138721 0.42113336]]
  f(x):  [-1.48016708]
acquisition funciton optimization tolerance changed to:  0.14801670833209823
Next points to be requested: 
[[6.91138721 0.42113336]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [0.44999403 1.11180932 3.2205079 ]



iteration:  22
Run Time:  0.22615361213684082      seconds
Number o

differential_evolution step 1: f(x)= -1.29871
differential_evolution step 2: f(x)= -1.32056
The acquisition function optimization resulted in: 
     x:  [[7.47212679 2.94147948]]
  f(x):  [-1.32056292]
acquisition funciton optimization tolerance changed to:  0.13205629198122074
Next points to be requested: 
[[7.47212679 2.94147948]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [0.44999403 1.11180932 3.2205079 ]



iteration:  32
Run Time:  0.6333878040313721      seconds
Number of measurements:  32
hps:  [0.44999403 1.1118093

differential_evolution step 2: f(x)= -1.25686
differential_evolution step 3: f(x)= -1.31717
differential_evolution step 4: f(x)= -1.31717
The acquisition function optimization resulted in: 
     x:  [[4.6419269 9.539354 ]]
  f(x):  [-1.31716794]
acquisition funciton optimization tolerance changed to:  0.13171679430111713
Next points to be requested: 
[[4.6419269 9.539354 ]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
async training is being killed
no training to be killed
    Fresh optimization from scratch via global optimization
fvGP training started with  41  data points
fvGP hyperparameter tuning in progress. Old hyperparameters:  [0.44999403 1.11180932 3.2205079 ]  with old log likelihood:  30.68716299547253
method:  local
fvGP is performing a local update of the hyper

...

differential_evolution step 6: f(x)= -1.066
differential_evolution step 7: f(x)= -1.066
differential_evolution step 8: f(x)= -1.0708
The acquisition function optimization resulted in: 
     x:  [[7.79157224 0.57949809]]
  f(x):  [-1.07079559]
acquisition funciton optimization tolerance changed to:  0.10707955859974744
Next points to be requested: 
[[7.79157224 0.57949809]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [0.77781135 5.37159927 8.33116791]



iteration:  72
Run Time:  3.3581161499023438      seconds
Number of meas

differential_evolution step 6: f(x)= -1.06537
differential_evolution step 7: f(x)= -1.06537
differential_evolution step 8: f(x)= -1.06537
The acquisition function optimization resulted in: 
     x:  [[7.74389416 1.71888879]]
  f(x):  [-1.06536792]
acquisition funciton optimization tolerance changed to:  0.10653679236119827
Next points to be requested: 
[[7.74389416 1.71888879]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [0.77781135 5.37159927 8.33116791]



iteration:  77
Run Time:  3.7861216068267822      seconds
Number of

differential_evolution step 1: f(x)= -1.05218
differential_evolution step 2: f(x)= -1.05218
differential_evolution step 3: f(x)= -1.05218
differential_evolution step 4: f(x)= -1.05218
differential_evolution step 5: f(x)= -1.05218
differential_evolution step 6: f(x)= -1.05218
differential_evolution step 7: f(x)= -1.05218
The acquisition function optimization resulted in: 
     x:  [[7.71678119 1.30407244]]
  f(x):  [-1.05218216]
acquisition funciton optimization tolerance changed to:  0.10521821611768663
Next points to be requested: 
[[7.71678119 1.30407244]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
The autonomous experimenter co

differential_evolution step 4: f(x)= -1.04118
differential_evolution step 5: f(x)= -1.04118
differential_evolution step 6: f(x)= -1.04118
The acquisition function optimization resulted in: 
     x:  [[1.36942004 0.76310973]]
  f(x):  [-1.04117802]
acquisition funciton optimization tolerance changed to:  0.1041178019389198
Next points to be requested: 
[[1.36942004 0.76310973]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [ 0.91237602  7.69458248 12.5483337 ]



iteration:  90
Run Time:  5.018938302993774      seconds
Number o

differential_evolution step 2: f(x)= -1.03361
differential_evolution step 3: f(x)= -1.03361
differential_evolution step 4: f(x)= -1.03889
differential_evolution step 5: f(x)= -1.03889
differential_evolution step 6: f(x)= -1.04129
The acquisition function optimization resulted in: 
     x:  [[7.72691528 1.49794812]]
  f(x):  [-1.0412945]
acquisition funciton optimization tolerance changed to:  0.10412944969907603
Next points to be requested: 
[[7.72691528 1.49794812]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [ 0.91237602  






## Now let's plot the posterior mean after the experiment has concluded

In [7]:
res = my_ae.gp_optimizer.posterior_mean(x_pred)
f = res["f(x)"]
f = f.reshape(100,100)

plot(x,y,f, data = np.column_stack([my_ae.x,my_ae.y]))

## Running a Multi-Task GP Autonomous Data Acquisition
This example uses 21 (!) dim robot data and 7 tasks, which you can all use or pick a subset of them

In [12]:
##prepare some data
import numpy as np
from scipy.interpolate import griddata
data = np.load("sarcos.npy")
print(data.shape)
x = data[:,0:21]
y = data[:,21:23]

(4449, 28)


In [13]:
from gpcam.autonomous_experimenter import AutonomousExperimenterFvGP


def instrument(data):
    for entry in data:
        entry["values"] = griddata(x,y,entry["position"],method = "nearest", fill_value = 0)[0]
        entry["value positions"] = np.array([[0],[1]])
    return data

input_s = np.array([np.array([np.min(x[:,i]),np.max(x[:,i])]) for i in range(len(x[0]))])
print("index set (input space) bounds:")
print(input_s)
print("hps bounds:")
hps_bounds = np.empty((22,2))
hps_bounds[:,0] = 0.0001
hps_bounds[:,1] = 100.0
hps_bounds[0] = np.array([0.0001, 10000])
print(hps_bounds)
print("shape of y: ")
print(y.shape)

my_fvae = AutonomousExperimenterFvGP(input_s,2,1,instrument,np.ones((22)),hps_bounds,
                                     init_dataset_size= 10)
my_fvae.train()
my_fvae.go(N = 100)

index set (input space) bounds:
[[ -0.842481   0.661032]
 [ -0.939933  -0.085018]
 [ -0.46773    0.359348]
 [  0.797788   2.239407]
 [ -0.242241   1.278097]
 [ -0.919895   0.369078]
 [ -0.296364   0.686928]
 [ -4.771399   4.488624]
 [ -1.634053   2.289369]
 [ -2.884804   2.558282]
 [ -4.196409   3.734968]
 [ -3.067483   2.380553]
 [ -2.433971   1.978575]
 [ -3.180643   2.568279]
 [-48.072386  48.872604]
 [-25.585054  25.225171]
 [-24.697862  26.106756]
 [-36.19139   71.176937]
 [-38.485967  35.804308]
 [-22.103174  17.84188 ]
 [-36.502723  30.806254]]
hps bounds:
[[1.e-04 1.e+04]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]]
shape of y: 
(4449, 2)
CAUTION: fvGP reports that you h

differential_evolution step 1: f(x)= -14.3865
The acquisition function optimization resulted in: 
     x:  [[  0.47978771  -0.32925199   0.23091104   1.69857719   0.65116943
   -0.10396561   0.09031352   3.1417704   -0.71408914  -1.03227332
   -0.3371986   -0.95306211  -2.38490236  -0.90360963  48.73285597
  -25.31594167   9.61910757 -33.77555372  32.0540545    7.33214218
   27.54162602]]
  f(x):  [-14.38645477]
acquisition funciton optimization tolerance changed to:  1.438645476731249
Next points to be requested: 
[[  0.47978771  -0.32925199   0.23091104   1.69857719   0.65116943
   -0.10396561   0.09031352   3.1417704   -0.71408914  -1.03227332
   -0.3371986   -0.95306211  -2.38490236  -0.90360963  48.73285597
  -25.31594167   9.61910757 -33.77555372  32.0540545    7.33214218
   27.54162602]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++

differential_evolution step 1: f(x)= -13.9697
The acquisition function optimization resulted in: 
     x:  [[-3.60862154e-01 -5.90641108e-01  2.29024879e-01  1.99696091e+00
   3.22686347e-01 -1.94888982e-02  1.96469392e-01 -3.14706981e+00
   2.29873973e-01  2.03139973e+00  3.85769276e-01 -2.33004980e+00
  -2.11249009e+00  7.42732414e-01  2.06209721e+01 -1.72850749e+01
  -2.14253356e+01  6.71385502e+01 -3.08960519e+01 -1.85137887e+01
   2.71652160e+01]]
  f(x):  [-13.96966755]
acquisition funciton optimization tolerance changed to:  1.396966754503597
Next points to be requested: 
[[-3.60862154e-01 -5.90641108e-01  2.29024879e-01  1.99696091e+00
   3.22686347e-01 -1.94888982e-02  1.96469392e-01 -3.14706981e+00
   2.29873973e-01  2.03139973e+00  3.85769276e-01 -2.33004980e+00
  -2.11249009e+00  7.42732414e-01  2.06209721e+01 -1.72850749e+01
  -2.14253356e+01  6.71385502e+01 -3.08960519e+01 -1.85137887e+01
   2.71652160e+01]]
Sending request to instrument ...
Data received
Checking if data

differential_evolution step 1: f(x)= -13.5264
The acquisition function optimization resulted in: 
     x:  [[ -0.27026836  -0.69930207   0.24959409   1.94857166   0.60273176
   -0.20027691  -0.22487156   2.8757004   -0.44527702  -0.28297587
   -0.29628433  -1.41574841   0.21125175  -0.53990305  48.24433969
   24.69468385  19.82159562 -31.31443791   3.85322086 -11.57313331
  -35.65520755]]
  f(x):  [-13.5263643]
acquisition funciton optimization tolerance changed to:  1.3526364302266287
Next points to be requested: 
[[ -0.27026836  -0.69930207   0.24959409   1.94857166   0.60273176
   -0.20027691  -0.22487156   2.8757004   -0.44527702  -0.28297587
   -0.29628433  -1.41574841   0.21125175  -0.53990305  48.24433969
   24.69468385  19.82159562 -31.31443791   3.85322086 -11.57313331
  -35.65520755]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++

differential_evolution step 1: f(x)= -13.1192
The acquisition function optimization resulted in: 
     x:  [[  0.15923079  -0.22125392  -0.37648626   2.15794232   0.09485913
    0.11529799  -0.14303486  -1.70919256   1.30610757  -1.73785513
    0.85235618   0.96184436  -0.29747018   2.05063073  38.82613395
  -21.71979429 -22.5601748   32.68422136  27.28868016  -7.46588167
  -29.56509699]]
  f(x):  [-13.11917104]
acquisition funciton optimization tolerance changed to:  1.3119171035548722
Next points to be requested: 
[[  0.15923079  -0.22125392  -0.37648626   2.15794232   0.09485913
    0.11529799  -0.14303486  -1.70919256   1.30610757  -1.73785513
    0.85235618   0.96184436  -0.29747018   2.05063073  38.82613395
  -21.71979429 -22.5601748   32.68422136  27.28868016  -7.46588167
  -29.56509699]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
+++++++++

...

differential_evolution step 1: f(x)= -11.6694
The acquisition function optimization resulted in: 
     x:  [[-1.73833288e-01 -4.24272252e-01 -3.02042084e-02  1.82950921e+00
   5.95064499e-01 -8.87442060e-01 -1.15041608e-01 -4.32847133e-02
   3.56458164e-01  2.39472046e+00  3.25869362e+00 -1.39034491e+00
  -2.20450361e+00 -2.70891353e+00  4.57838567e+01 -2.01970281e+01
   2.30471554e+01  3.41303622e+01 -3.44135926e+01 -1.78168081e+01
   2.93017207e+01]]
  f(x):  [-11.66938144]
acquisition funciton optimization tolerance changed to:  1.1669381443620914
Next points to be requested: 
[[-1.73833288e-01 -4.24272252e-01 -3.02042084e-02  1.82950921e+00
   5.95064499e-01 -8.87442060e-01 -1.15041608e-01 -4.32847133e-02
   3.56458164e-01  2.39472046e+00  3.25869362e+00 -1.39034491e+00
  -2.20450361e+00 -2.70891353e+00  4.57838567e+01 -2.01970281e+01
   2.30471554e+01  3.41303622e+01 -3.44135926e+01 -1.78168081e+01
   2.93017207e+01]]
Sending request to instrument ...
Data received
Checking if dat

  f(x):  [-9.93282271]
acquisition funciton optimization tolerance changed to:  0.9932822708008422
Next points to be requested: 
[[ -0.684198    -0.42869332   0.09117509   1.93715743   0.14687531
    0.08228931   0.19950745   1.56714266   1.24849452   0.65806509
    2.12372313  -1.26480666  -1.76162284   0.85307656   4.11475693
  -20.13995216  -6.76579495   5.26279098  14.63024431 -19.58980109
   25.20709223]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [235.15120058  78.57711928  74.64374101  44.08583977  97.74948166
  63.50006539  76.76914295  74.89928512  96.61913634  8

differential_evolution step 1: f(x)= -11.2881
The acquisition function optimization resulted in: 
     x:  [[  0.32484482  -0.33019205  -0.08172584   1.93264985  -0.15473539
   -0.73290821   0.32257065  -3.37408689   1.61943655  -2.77982584
    2.59063271  -2.39875474  -2.09687811   1.1277389    5.15749436
   10.40104072  20.89881569  15.32158755  35.45303118 -21.56670299
   23.67928469]]
  f(x):  [-11.28811789]
acquisition funciton optimization tolerance changed to:  1.128811789440541
Next points to be requested: 
[[  0.32484482  -0.33019205  -0.08172584   1.93264985  -0.15473539
   -0.73290821   0.32257065  -3.37408689   1.61943655  -2.77982584
    2.59063271  -2.39875474  -2.09687811   1.1277389    5.15749436
   10.40104072  20.89881569  15.32158755  35.45303118 -21.56670299
   23.67928469]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++

Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [235.15120058  78.57711928  74.64374101  44.08583977  97.74948166
  63.50006539  76.76914295  74.89928512  96.61913634  87.40601111
  39.00185553  71.22669194  82.06253092  95.31053526  94.25284101
  98.39625754  99.97349024  93.29465249  21.72121125  99.12795967
  89.56026852  57.2598696 ]



iteration:  96
Run Time:  32.467159032821655      seconds
Number of measurements:  96
hps:  [235.15120058  78.57711928  74.64374101  44.08583977  97.74948166
  63.50006539  76.76914295  74.89928512  96.61913634  87.40601111
  39.00185553  71.22669194  82.06253092  95.310535

differential_evolution step 1: f(x)= -11.4481
The acquisition function optimization resulted in: 
     x:  [[ -0.18185388  -0.68955559   0.13071313   1.18123941   1.0880354
   -0.19893623  -0.2125516   -1.16076439   1.87336092   0.38571917
   -1.5199019   -2.15043701   1.25300463  -1.50618513 -45.98868105
  -22.20126843 -21.15889259   9.34512847  33.40585003 -11.92692437
  -27.99329797]]
  f(x):  [-11.44805014]
acquisition funciton optimization tolerance changed to:  1.1448050138345118
Next points to be requested: 
[[ -0.18185388  -0.68955559   0.13071313   1.18123941   1.0880354
   -0.19893623  -0.2125516   -1.16076439   1.87336092   0.38571917
   -1.5199019   -2.15043701   1.25300463  -1.50618513 -45.98868105
  -22.20126843 -21.15889259   9.34512847  33.40585003 -11.92692437
  -27.99329797]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
+++++++++++

## Plotting the 0th task in a 2d slice

In [14]:
x_pred = np.zeros((10000,21))
x = np.linspace(input_s[0,0],input_s[0,1],100)
y = np.linspace(input_s[1,0],input_s[1,1],100)
x,y = np.meshgrid(x,y)
counter = 0
for i in  range(100):
    for j in range(100):
        x_pred[counter] = np.zeros((21))
        x_pred[counter,[0,1]] = np.array([x[i,j],y[i,j]])
        counter += 1
res = my_fvae.gp_optimizer.posterior_mean(x_pred)
f = res["f(x)"]
f = f.reshape(100,100)

plot(x,y,f)

## Back to a single task: using the GPOptimizer class directly gives you some more flexibility
We will show more soon!

In [15]:
#/usr/bin/env python
import numpy as np
from gpcam.gp_optimizer import GPOptimizer

#initialize some data
x_data = np.random.uniform(size = (100,1))
y_data = np.sin(x_data)[:,0]


#initialize the GPOptimizer
my_gpo = GPOptimizer(1,np.array([[0,1]]))
#tell() it some data
my_gpo.tell(x_data,y_data)
#initialize a GP ...
my_gpo.init_gp(np.ones(2))
#and train it
my_gpo.train_gp(np.array([[0.001,100],[0.001,100]]))

#let's make a prediction
print(my_gpo.posterior_mean(np.array([0.44])))

#now we can ask for a new point
r = my_gpo.ask()
print(r)
#putting the ask() in a loop and updating the data will
#give you all you need for your autonomous experiment

New data communicated via tell()
CAUTION: you have not provided data variances in fvGP,
they will be set to 1 percent of the data values!
GP successfully initiated
fvGP training started with  100  data points
fvGP hyperparameter tuning in progress. Old hyperparameters:  [1. 1.]  with old log likelihood:  -96.29720526805555
method:  global
fvGP is performing a global differential evolution algorithm to find the optimal hyperparameters.
maximum number of iterations:  120
termination tolerance:  1e-06
bounds:  [[1.e-03 1.e+02]
 [1.e-03 1.e+02]]
differential_evolution step 1: f(x)= -158.785
differential_evolution step 2: f(x)= -159.129
differential_evolution step 3: f(x)= -159.129
differential_evolution step 4: f(x)= -159.129
differential_evolution step 5: f(x)= -159.309
differential_evolution step 6: f(x)= -159.552
differential_evolution step 7: f(x)= -159.552
differential_evolution step 8: f(x)= -159.552
differential_evolution step 9: f(x)= -159.591
differential_evolution step 10: f(x)= 